# Self-Supervised предобучение на примере MoCo v2

## Введение

Чаще всего специалисты в области компьютерного зрения для дообучения (fine-tuning) нейронных сетей под конкретную задачу берут за основу веса, полученные после их обучения в supervised режиме (обучение с учителем) на каком-то большом наборе данных (датасете), например, ImageNet. Считается, что предобученные таким образом нейросети имеют лучшую обобщающую способность и могут быстрее научиться решать другие задачи.

Однако такой подход требует большого предварительно размеченного датасета, а также часты случаи, когда имеющиеся крупные наборы данных с разметкой по типу ImageNet имеют совершенно другой домен, чем те данные, на которых вы хотите дообучить сеть. То есть, например, если перед вами стоит цель обучить нейронную сеть, способную находить патологии на рентгенограммах, то вполне вероятно, что нейросеть, предварительно обученная на 1000 классах различных объектов из ImageNet, может не совсем хорошо дообучиться под конечную задачу. Интуитивно можно предположить, что сеть, предобученная каким-то образом на медицинских снимках, может справиться с данной задачей намного лучше. Именно поэтому в последнее время в научной среде начала получать развитие техника self-supervised предобучения.

## Что такое self-supervised предобучение?

**Self-Supervised предобучение (self-supervised pre-training, самообучение)** — способ предварительного обучения нейронной сети с помощью данных без разметки (или с разметкой, полученной «дешевым» способом) с целью формирования хороших ее первичных признаков. Чаще всего такое предобучение достигается за счет постановки какой-то относительно простой задачи, данные для которой можно генерировать «налету».

Примеры таких задач:
- Предсказать контекст [1] — изоображение делится на патчи (на квадраты, как мозаика) и некоторые случайные патчи из него удаляются, а перед нейросетью ставится задача восстановить удаленные патчи
- Разгадать пазл [2] — как и в предудщей задаче картинка делится на патчи и после чего они перемешиваются. Сети необходимо восстановить первичное изображение до перемешивания патчей, то есть переставить патчи в верном порядке
- Предсказать угол поворота картинки [3] — изображение поворачивается на случайный угол и нейронной сети нужно предсказать угол поворота

Выше описаны только некоторые примеры задач, которые можно «попросить» нейронную сеть решить для ее предварительного обучения и формирования у нее хороших первичных признаков на данных, похожих на те, что будут использоваться для дообучения под конечную задачу. И, как вы уже могли заметить, во всех примерах можно применять датасеты, состоящие исключительно из картинок без разметки, последнюю можно получать «налету» в автоматическом режиме.

Резюмируя изложенное выше, при процессе самообучения чаще всего нейросети на данных из домена, схожего с конечным доменом, ставится относительно простая задача, которую она пытается решать и тем самым учится формировать какие-то первичные признаки. После чего эта нейросеть дообучается на данных для конечной задачи. Self-Supervised предобучение можно назвать успешным, если в итоге ваша нейронная сеть сможет решать конечную задачу лучше, чем сеть, обученная по «стандартной» схеме (то есть дообучалась нейросеть, предварительно обученная в supervised режиме на крупном датасете).

## MoCo и MoCo v2

Большинство современных self-supervised подходов основаны на идее контрастивного обучения (contrastive learning). Суть последней заключается в том, что нейронная сеть обучается сближать в пространстве «позитивные» примеры (изображения одного класса) и отдалять друг от друга «негативные» примеры (соответственно, изображения разных классов) — это достигается за счет следующей функции потерь:
$\begin{equation}
    \begin{split}
      \mathcal{L}_{contrastive} &= \mathbb{E} \left[ -\log{\frac{\exp(q \cdot k^+ / \tau)}{\exp(q \cdot k^+ / \tau) + \sum\nolimits_{j=0}^{K - 1} \exp(q \cdot k^-_j / \tau)}} \right],
    \end{split}
\end{equation}$
где ${q}$ — векторное представление «изображения-запроса», ${k^+}$ и ${k^-}$ — векторные представления «позитивного» и «негативных» для «изображения-запроса» примеров, соответственно, а ${\tau}$ — параметр «температуры».

Одним из уже ставших «классическим» подходом является стратегия MoCo [4]. На рисунке ниже представлена схема данного метода:

![](https://courses.cv-gml.ru/storage/seminars/self-supervised/moco_scheme.png "Схема метода MoCo")

Его идея следующая:
- К входному изображению применяются две аугментации
- Далее одно аугментированное изображение попадает в кодировщик (encoder), другое — в моментум-кодировщик (momentum encoder)
- Выходами encoder и momentum encoder являются векторные представления изображений, которые используются при вычислении Contrastive Loss — функции потерь, описанной выше (две аугментации принимаются за «позитивные» примеры, примеры из очереди — за «негативные»)
- Вектор, полученный из momentum encoder, добавляется в конец очереди. Последняя строится по стратегии FIFO
- Веса momentum encoder обновляются за счет моментум-усреднения весов encoder: $\theta^{t}_{m} = {\alpha \theta^{t-1}_{m} + (1 - \alpha) \theta^{t}_{e}}$, где ${\theta^{t}_{e}}$ и ${\theta^{t}_{m}}$ — веса кодировщика и моментум-кодировщика на ${t}$-ой итерации, соответственно, а ${\alpha}$ — коэффициент момента (в оригинальном варианте ${\alpha = \text{0,999}}$)

### Зачем нужна очередь?
Во множестве работ, посвященных самообучению, было показано, что для хорошего контрастивного обучения необходимо много «негативных» примеров при вычислении Contrastive Loss. В методе SimCLR [5] этого предложили достичь за счет батча большого размера, а в [6] — с помощью memory bank, в котором находятся векторные представления всех изображений из датасета. Как вы уже могли догадаться, оба подхода требуют большого объема видеопамяти и вычислительно затратны (для каждой картинки необходимо считать градиенты и делать backpropagation).

В MoCo же используется большая очередь, полученная из momentum encoder, все элементы которой берутся в качестве «негативных» примеров при вычислении Contrastive Loss. И так как очередь обновляется постепенно после каждого изменения весов в momentum encoder, то для элементов очереди не нужно считать и хранить градиенты при вычислении функции потерь и, соответственно, делать обратное распространение ошибок. Тем самым стратегия MoCo является наиболее эффективной с точки зрения вычислительных затрат по сравнению с другими упомянутыми подходами и при этом решает вопрос с необходимостью большого числа «негативных» примеров для лучшего контрастивного обучения.

### Зачем нужно моментум-усреднение?
Так как self-supervised предобучение подразумевает обучение нейронной сети с нуля (то есть практически со случайных весов), то для бо́льшей устойчивости веса сети нужно обновлять постепенно. Таким образом momentum encoder, а именно его веса в дальнейшем используются для дообучения под конечную задачу, наиболее устойчив к шуму.

### Чем MoCo отличается от MoCo v2?
Выше была описана идея метода MoCo. Однако чаще исследователями применяется вторая его версия MoCo v2 [7], которая отличается от первой следующими моментами:
- Используется больше аугментаций изображений
- В «стандартом» подходе в качестве выходов encoder и momentum encoder брались 128-мерные векторы после полносвязного слоя. В MoCo v2 используется Projection Head — последовательность нескольких полносвязных слоев между которыми добавлена нелинейность в виде функции активации ReLU

На самом деле, существует еще и MoCo v3 [8], но данный метод преследует ту же идею, что и два его предшественника, и больше ориентирован на трансформерные архитектуры. Поэтому далее мы рассмотрим то, как можно реализовать схему self-supervised предобучения MoCo v2 на PyTorch. 

## Реализация MoCo v2 на PyTorch

In [ ]:
import math
import os

import cv2
import matplotlib.pyplot as plt
import numpy as np
import torch
import torchvision
import torchvision.models as models
import torchvision.transforms.v2 as transforms
from PIL import Image
from torch.nn import functional as F
from torch.utils import data
from tqdm.notebook import tqdm

# Increase these if figures appear small
plt.rcParams["figure.figsize"] = fx, fy = (14.08, 6.40)

In [ ]:
# Определение констант
MEAN = [0.485, 0.456, 0.406]
STD = [0.229, 0.224, 0.225]
EPOCHS = 100
LR = 0.001

In [ ]:
# Включает демонстрационный режим (загружаются готовые веса вместо обучения моделей)
FAST = True

### Определение основного класса MoCo v2

In [ ]:
class MoCoV2(torch.nn.Module):
    def __init__(self, K=65536, m=0.999, T=0.07, symmetric=True):
        super().__init__()

        self.K = K
        self.m = m
        self.T = T
        self.symmetric = symmetric

        # Инициализируем encoder (encoder_q) и momentum encoder (encoder_k)
        self.encoder_q = torchvision.models.resnet50()
        self.encoder_k = torchvision.models.resnet50()

        # Инициализируем Projection Head для encoder и momentum encoder
        self.encoder_q.fc = self.get_projection_head()
        self.encoder_k.fc = self.get_projection_head()

        for param_q, param_k in zip(
            self.encoder_q.parameters(),
            self.encoder_k.parameters(),
        ):
            # Копируем веса из обычного encoderа в momentum  encoder,
            # чтобы в начале обучения они были одинаковыми
            param_k.data.copy_(param_q.data)

            # Веса momentum encoder обновлять не нужно
            param_k.requires_grad = False

        # Создаем очередь
        self.register_buffer("queue", torch.randn(128, K))
        self.queue = F.normalize(self.queue, dim=0)

        # Создаем указатель на текущее место в очереди
        self.register_buffer("queue_ptr", torch.zeros(1, dtype=torch.long))

    def get_projection_head(self):
        """
        Функция создания Projection Head
        """
        projection_head = torch.nn.Sequential(
            torch.nn.Linear(2048, 2048),
            torch.nn.ReLU(),
            torch.nn.Linear(2048, 128),
        )
        return projection_head

    @torch.no_grad()
    def _momentum_update_key_encoder(self):
        """
        Функция для обновления весов momentum encoder с помощью моментум-усреднения
        """
        for param_q, param_k in zip(
            self.encoder_q.parameters(),
            self.encoder_k.parameters(),
        ):
            param_k.data = param_k.data * self.m + param_q.data * (1.0 - self.m)

    @torch.no_grad()
    def _dequeue_and_enqueue(self, keys):
        """
        Функция обновления очереди
        """
        batch_size = keys.shape[0]
        ptr = int(self.queue_ptr)

        # Для простоты считаем что очередь состоит из целых батчей
        assert self.K % batch_size == 0

        # Удаляем старые элементы очереди и добавляем новые (FIFO)
        self.queue[:, ptr : ptr + batch_size] = keys.T

        # Сдвигаем указатель очереди
        ptr = (ptr + batch_size) % self.K

        self.queue_ptr[0] = ptr

    def contrastive_loss(self, im_q, im_k):
        """
        Функция вычисления Сontrastive Loss
        """
        # Вычисляем выходы encoder
        # queries: NxC
        q = self.encoder_q(im_q)
        # Нормализуем выходы
        q = F.normalize(q, dim=1)

        # Вычисляем выходы momentum encoder
        with torch.no_grad():
            # keys: NxC
            k = self.encoder_k(im_k)
            # Нормализуем выходы
            k = F.normalize(k, dim=1)

        # Вычисляем logits
        # "Позитивные" logits: Nx1
        l_pos = torch.einsum("nc,nc->n", [q, k]).unsqueeze(-1)
        # "Негативные" logits, "негативные" примеры берем из очереди: NxK
        l_neg = torch.einsum("nc,ck->nk", [q, self.queue.clone().detach()])

        # Объединяем logits в один тензор: Nx(1+K)
        logits = torch.cat([l_pos, l_neg], dim=1)

        # Применяем температуру согласно формуле Сontrastive Loss
        logits /= self.T

        # Метки — в данном случае это индексы "позитивных" пар,
        # То есть это logits, расположенные в нулевом столбце тензора
        labels = torch.zeros(logits.shape[0], dtype=torch.long).cuda()

        # Свели Contrastive Loss к "стандартным" Softmax + Cross Entropy
        loss = F.cross_entropy(logits, labels)

        return loss, q, k

    def forward(self, im1, im2):
        # Обновляем momentum encoder с помощью моментум-усреднения
        self._momentum_update_key_encoder()

        # Вычисляем функцию потерь
        if self.symmetric:
            # Симметричное вычисление функции потерь
            loss_12, q1, k2 = self.contrastive_loss(im1, im2)
            loss_21, q2, k1 = self.contrastive_loss(im2, im1)
            loss = loss_12 + loss_21
            k = torch.cat([k1, k2], dim=0)
        else:
            # Асимметричное вычисление функции потерь
            loss, q, k = self.contrastive_loss(im1, im2)

        # Обновление очереди
        self._dequeue_and_enqueue(k)

        return loss

In [ ]:
# Инициализация MoCo v2 и перенос модели на GPU
model = MoCoV2().cuda()

### Подготовка данных

In [ ]:
class ImageNetPair(torchvision.datasets.ImageNet):
    """
    Обертка над torchvision-версией датасета ImageNet
    для генерации двух аугментаций одного изображения
    """

    def __getitem__(self, index):
        img = self.data[index]
        img = Image.fromarray(img)

        if self.transform is not None:
            im_1 = self.transform(img)
            im_2 = self.transform(img)

        return im_1, im_2

In [ ]:
# Определение аугментаций
train_transform = transforms.Compose(
    [
        transforms.RandomResizedCrop(224),
        transforms.RandomHorizontalFlip(p=0.5),
        transforms.RandomApply(
            [transforms.ColorJitter(0.4, 0.4, 0.4, 0.1)],
            p=0.8,
        ),
        transforms.RandomGrayscale(p=0.2),
        transforms.ToImage(),
        transforms.ToDtype(torch.float32, scale=True),
        transforms.Normalize(mean=MEAN, std=STD),
    ],
)

In [ ]:
if not FAST:
    # Скачивание изображений ImageNet
    # АХТУНГ! Требуется ~150 GB места на диске!
    !mkdir -p imagenet
    for f in [
        "ILSVRC2012_devkit_t12.tar.gz",
        "ILSVRC2012_img_train.tar",
        "ILSVRC2012_img_val.tar",
    ]:
        if not os.path.exists(f"imagenet/{f}"):
            !curl -O 'https://image-net.org/data/ILSVRC/2012/{f}' --output-dir imagenet/

    # Инициализация датасета
    train_data = ImageNetPair(
        root="imagenet",
        train=True,
        transform=train_transform,
        download=True,
    )

    # Инициализация DataLoader
    train_loader = data.DataLoader(
        train_data,
        batch_size=32,
        shuffle=True,
        num_workers=8,
        pin_memory=True,
        drop_last=True,
    )

### Обучение

In [ ]:
def adjust_learning_rate(lr, optimizer, epoch):
    """
    Scheduler для learning rate
    """
    # Cosine lr schedule
    lr *= 0.5 * (1.0 + math.cos(math.pi * epoch / EPOCHS))

    for param_group in optimizer.param_groups:
        param_group["lr"] = lr


def train(model, train_loader, optimizer, epoch, lr):
    """
    Функция обучения в течение одной эпохи
    """
    model.train()
    adjust_learning_rate(
        lr,
        optimizer,
        epoch,
    )

    total_loss = 0.0
    for im_1, im_2 in tqdm(train_loader):
        im_1 = im_1.cuda()
        im_2 = im_2.cuda()

        loss = model(im_1, im_2)

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    print(
        f"Epoch #{epoch + 1}",
        f"Loss: {total_loss / len(train_loader):.3f}",
    )

In [ ]:
if not FAST:
    # Определяем оптимизатор SGD
    optimizer = torch.optim.SGD(
        model.parameters(),
        lr=LR,
        momentum=0.9,
    )

    # Цикл обучения
    for epoch in range(EPOCHS):
        train(model, train_loader, optimizer, epoch, LR)

    # Сохраняем обученный энкодер
    os.makedirs("weights", exist_ok=True)
    torch.save(
        model.encoder_q.state_dict(),
        f"weights/resnet50_mocov2_pretrained.pth",
    )

In [ ]:
if not os.path.exists("weights/"):
    !curl -O https://courses.cv-gml.ru/storage/seminars/self-supervised/weights.zip
    !unzip -o weights.zip

## Дообучение модели, предобученной с помощью MoCo v2

В рамках данного Jupyter Notebook будет продемонстрирована процедура дообучения (fine-tuning) нейронной сети, предобученной в self-supervised режиме с помощью стратегии MoCo v2 на наборе данных ImageNet, для задачи классификации изображений из датасета CIFAR-10.

Датасет CIFAR-10 состоит из картинок 10 классов: самолет, машина, птица, кошка, олень, собака, лягушка, лошадь, корабль и грузовик. Все изображения цветные и по умолчанию имеют размер 32x32 пикселей.

Мы покажем, что если заморозить все слои сети, предобученные в self-supervised режиме, кроме последнего классификационного полносвязного слоя, то можно добиться лучшего качества решения поставленной задачи, чем если полностью обучать нейронную сеть с нуля на датасете CIFAR-10 в supervised режиме в течение бо́льшего числа эпох.

### Вспомогательные функции для работы с данными

In [ ]:
def prepare_data(batch_size, num_workers):
    """
    Функция для подготовки данных и DataLoader
    """
    # Определение преобразований
    transform = transforms.Compose(
        [
            transforms.Resize((224, 224)),
            transforms.ToImage(),
            transforms.ToDtype(torch.float32, scale=True),
            transforms.Normalize(
                mean=MEAN,
                std=STD,
            ),
        ],
    )
    # Инициализация обучающей выборки датасета CIFAR-10 и DataLoader для нее
    trainset = torchvision.datasets.CIFAR10(
        root="cifar10/",
        train=True,
        download=True,
        transform=transform,
    )
    trainloader = data.DataLoader(
        trainset,
        batch_size=batch_size,
        shuffle=True,
        num_workers=num_workers,
    )

    # Инициализация обучающей выборки датасета CIFAR-10 и DataLoader для нее
    testset = torchvision.datasets.CIFAR10(
        root="cifar10/",
        train=False,
        download=True,
        transform=transform,
    )
    testloader = data.DataLoader(
        testset,
        batch_size=batch_size,
        shuffle=False,
        num_workers=num_workers,
    )

    return trainloader, testloader

In [ ]:
def show_images(img):
    """
    Вспомогательная функция для демонстрации изображений из датасета
    """
    # "обратная" нормализация
    unnormalize = transforms.Normalize(
        mean=(-torch.Tensor(MEAN) / torch.Tensor(STD)).tolist(),
        std=(1.0 / torch.Tensor(STD)).tolist(),
    )
    img = unnormalize(img).numpy().clip(0, 1)

    plt.imshow(np.transpose(img, (1, 2, 0)))
    plt.show()

In [ ]:
trainloader, testloader = prepare_data(batch_size=32, num_workers=8)

### Визуализация изображений из CIFAR-10 

In [ ]:
dataiter = iter(trainloader)
images, labels = next(dataiter)

show_images(torchvision.utils.make_grid(images))

### Эксперименты с нейронной сетью, предобученной с помощью MoCo v2

In [ ]:
# Инициализируем ResNet50
model_moco_pretrained = models.resnet50()

In [ ]:
# Удаляем классификационный слой и Average Pooling из ResNet50
model_moco_pretrained.avgpool = torch.nn.Identity()
model_moco_pretrained.fc = torch.nn.Identity()

In [ ]:
# Загружаем веса, предобученные с помощью MoCo v2
model_moco_pretrained.load_state_dict(
    torch.load(
        "weights/resnet50_mocov2_pretrained.pth",
        map_location="cuda",
        weights_only=True,
    ),
)
model_moco_pretrained = model_moco_pretrained.to("cuda")

#### Визализация карт активаций сети

In [ ]:
def visactmap(model, images, width, height, device="cuda", img_mean=MEAN, img_std=STD):
    """
    Функция визуализации карт активаций
    """
    # Не забываем перевести модель в inference-режим
    model.eval()
    with torch.no_grad():
        images = images.to(device=device)
        outputs = model(images)

    # Вычисление карт активаций
    outputs = outputs.reshape(-1, 2048, 7 * 7)
    outputs = outputs.square().sum(axis=1)
    outputs = F.normalize(outputs, dim=1)
    outputs = outputs.view(-1, 7, 7)

    images, outputs = images.cpu(), outputs.cpu()

    results = []
    for j in range(outputs.shape[0]):
        # Преобразуем изображение обратно в RGB после нормализации
        img = images[j]
        for t, m, s in zip(img, img_mean, img_std):
            t.mul_(s).add_(m).clamp_(0, 1)

        # CHW (float 0-1) -> HWC (uint8 0-255)
        img_np = np.uint8(np.floor(img.numpy() * 255))
        img_np = img_np.transpose((1, 2, 0))

        # Изображение карты активаций
        am = outputs[j].numpy()
        target = (width, height)
        am = cv2.resize(am, target, interpolation=cv2.INTER_NEAREST)
        am = 255 * (am - np.min(am)) / (np.max(am) - np.min(am) + 1e-12)
        am = np.uint8(np.floor(am))
        am = cv2.applyColorMap(am, cv2.COLORMAP_MAGMA)

        # Карта активаций, наложенная на исходную картинку
        overlapped = img_np * 0.7 + am * 0.7
        overlapped = overlapped.clip(0, 255)
        overlapped = overlapped.astype(np.uint8)

        # Сохранение изображений
        # слева-направо: оригинальная картинка, карта активаций, наложенная карта активаций
        grid_img = 255 * np.ones(
            (height, 3 * width, 3),
            dtype=np.uint8,
        )
        grid_img[:, :width, :] = img_np
        grid_img[:, width : 2 * width, :] = am
        grid_img[:, 2 * width :, :] = overlapped

        results.append(grid_img)

    return results

In [ ]:
images_for_att_vis = images[:5]

vis_results = visactmap(
    model=model_moco_pretrained,
    images=images_for_att_vis,
    width=224,
    height=224,
)

for vis_res in vis_results:
    plt.imshow(vis_res)
    plt.show()

Как можно видеть из визуализаций, в большинстве случаев нейронная сеть относительно неплохо локализует объекты на изображениях и это несмотря на то, что она была предобученна на ImageNet и без разметки. Таким образом интуитивно можно предположить, что такая нейросеть может эффективнее дообучиться (по крайней мере, за меньшее число эпох) под конечную задачу, нежели сеть, которая будет обучаться решать конечную задачу с нуля.

#### Дообучение нейронной сети

In [ ]:
# Возвращаем Average Pooling
model_moco_pretrained.avgpool = torch.nn.AdaptiveAvgPool2d((1, 1)).to("cuda")

# Добавляем классификационный слой с 10 выходами (столько классов в CIFAR=10)
model_moco_pretrained.fc = torch.nn.Linear(2048, 10).to("cuda")

In [ ]:
# Замораживаем все слои, кроме последнего классификационного
for param_name, param in model_moco_pretrained.named_parameters():
    if "fc" not in param_name:
        param.requires_grad = False
    else:
        print(f"Param {param_name} skipped!")

In [ ]:
def train(model, epochs, trainloader, save_path):
    """
    Функция обучения нейронной сети для задачи классификации
    """
    criterion = torch.nn.CrossEntropyLoss()
    optimizer = torch.optim.Adam(
        model.parameters(),
        lr=0.01,
    )

    model.train()
    for epoch in range(epochs):
        running_loss = 0.0
        for data in tqdm(trainloader, 0):
            images, labels = data
            images = images.to("cuda")
            labels = labels.to("cuda")

            outputs = model(images)
            loss = criterion(outputs, labels)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            running_loss += loss.item()

        print(
            f"Epoch #{epoch + 1}",
            f"Loss: {running_loss / len(trainloader):.3f}",
        )
        running_loss = 0.0

    torch.save(
        model.state_dict(),
        f"weights/{exp_name}.pth",
    )

In [ ]:
save_path = "weights/model_moco_pretrained.pth"

if not FAST:
    # Если не выбран демонстрационный режим, то обучаем модель
    train(
        model=model_moco_pretrained,
        epochs=3,
        trainloader=trainloader,
        save_path=save_path,
    )

# Загружаем веса
model_moco_pretrained.load_state_dict(
    torch.load(
        save_path,
        map_location="cuda",
        weights_only=True,
    ),
);

In [ ]:
def test(model, testloader):
    """
    Функция тестирования нейронной сети для задачи классификации
    """
    correct = 0
    total = 0

    model.eval()
    with torch.no_grad():
        for data in testloader:
            images, labels = data
            images = images.to("cuda")
            labels = labels.to("cuda")

            outputs = model(images)
            predicted = outputs.data.argmax(axis=-1)

            total += labels.size(0)
            correct += (predicted == labels).sum().item()

    print(
        "Accuracy of the network on the 10000 test images:",
        f"{correct / total:.2%}",
    )

In [ ]:
# Тестирование модели
test(
    model=model_moco_pretrained,
    testloader=testloader,
)

### Эксперименты с обучением нейронной сети с нуля

In [ ]:
# Инициализируем ResNet50
model_without_pretrain = models.resnet50()

# Заменяем классификационный слой ImageNet на полносвязный
# слой с 10 выходами (столько классов в CIFAR=10)
model_without_pretrain.fc = torch.nn.Linear(2048, 10)

# Переносим модель на GPU
model_without_pretrain = model_without_pretrain.to("cuda")

In [ ]:
save_path = "weights/model_without_pretrain.pth"

if not FAST:
    # Если не выбран демонстрационный режим, то обучаем модель
    train(
        model=model_without_pretrain,
        epochs=5,
        trainloader=trainloader,
        save_path=save_path,
    )

# Загружаем веса
model_without_pretrain.load_state_dict(
    torch.load(
        save_path,
        map_location="cuda",
        weights_only=True,
    ),
);

In [ ]:
# Тестирование модели
test(
    model=model_without_pretrain,
    testloader=testloader,
)

Как можно видеть из результатов экспериментов, в случае использования модели, предобученной в self-supervised режиме по стратегии MoCo v2, после ее дообучения точность классификации на наборе данных CIFAR-10 составила 84%. А при полном обучении в supervised режиме всей нейросети за бо́льшее число эпох удалость достичь точности в 76%. Еще раз отметим, что в первом случае замораживались все слои нейронной сети, кроме последнего классификационного. Такой результат может говорить о том, что с помощью self-supervised предобучения сеть действительно учит первичные признаки и тем самым удается эффективнее дообучать модели.

### Эксперименты с нейронной сетью, предобученной в supervised режиме на ImageNet

In [ ]:
# Инициализируем ResNet50 и загружаем веса, предобученные на ImageNet
model_imagenet_pretrained = models.resnet50(weights="IMAGENET1K_V1")

# Заменяем классификационный слой ImageNet на полносвязный
# слой с 10 выходами (столько классов в CIFAR=10)
model_imagenet_pretrained.fc = torch.nn.Linear(2048, 10)

# Переносим модель на GPU
model_imagenet_pretrained = model_imagenet_pretrained.to("cuda")

In [ ]:
# Замораживаем все слои, кроме последнего классификационного
for param_name, param in model_imagenet_pretrained.named_parameters():
    if "fc" not in param_name:
        param.requires_grad = False
    else:
        print(f"Param {param_name} skipped!")

In [ ]:
save_path = "weights/model_imagenet_pretrained.pth"

if not FAST:
    # Если не выбран демонстрационный режим, то обучаем модель
    train(
        model=model_imagenet_pretrained,
        epochs=3,
        trainloader=trainloader,
        save_path=save_path,
    )

# Загружаем веса
model_imagenet_pretrained.load_state_dict(
    torch.load(
        save_path,
        map_location="cuda",
        weights_only=True,
    ),
);

In [ ]:
# Тестирование модели
test(
    model=model_imagenet_pretrained,
    testloader=testloader,
)

Как можно видеть из результатов этого эксперимента, предобученная модель с помощью стратегии MoCo v2 снова имеет наилучшие результаты качества решения задачи классификации на датасете CIFAR-10 после дообучения. Отдельно стоит отметить, что CIFAR-10 и ImageNet в чем-то похожи друг на друга. Как следует из большинства статей, посвященных самообучению, особый эффект от него заметен в случае, когда домен данных для конечной задачи серьезно отличается от домена ImageNet. И в таком случае, скорее всего, стоит сначала предобучить нейронную сеть с помощью MoCo v2 на неразмеченных данных, приближенных к конечным, а потом дообучиться.

## Список литературы

1. He, Kaiming, et al. "Masked autoencoders are scalable vision learners". Proceedings of the IEEE/CVF conference on computer vision and pattern recognition. 2022.
2. Noroozi, Mehdi, and Paolo Favaro. "Unsupervised learning of visual representations by solving jigsaw puzzles". arXiv preprint arXiv:1603.09246. 2016.
3. Gidaris, Spyros, Praveer Singh, and Nikos Komodakis. "Unsupervised representation learning by predicting image rotations". arXiv preprint arXiv:1803.07728. 2018.
4. He, Kaiming, et al. "Momentum contrast for unsupervised visual representation learning". Proceedings of the IEEE/CVF conference on computer vision and pattern recognition. 2020.
5. Chen, Ting, et al. "A simple framework for contrastive learning of visual representations". International conference on machine learning. PMLR, 2020.
6. Wu, Zhirong, et al. "Unsupervised feature learning via non-parametric instance discrimination". Proceedings of the IEEE conference on computer vision and pattern recognition. 2018.
7. Chen, Xinlei, et al. "Improved baselines with momentum contrastive learning". arXiv preprint arXiv:2003.04297. 2020.
8. Chen, Xinlei, Saining Xie, and Kaiming He. "An empirical study of training self-supervised vision transformers". Proceedings of the IEEE/CVF International Conference on Computer. Vol. 412. 2021.